Welcome to Tortoise! 🐢🐢🐢🐢

Before you begin, I **strongly** recommend you turn on a GPU runtime.

There's a reason this is called "Tortoise" - this model takes up to a minute to perform inference for a single sentence on a GPU. Expect waits on the order of hours on a CPU.

In [2]:
# the scipy version packaged with colab is not tolerant of misformated WAV files.
# install the latest version.
!pip3 install -U scipy

!git clone https://github.com/jnordberg/tortoise-tts.git
%cd tortoise-tts
!pip3 install transformers==4.19.0
!pip3 install -r requirements.txt
!python3 setup.py install

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
fatal: destination path 'tortoise-tts' already exists and is not an empty directory.
/content/tortoise-tts
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Using cached numba-0.48.0-cp39-cp39-linux_x86_64.whl
  Using cached ffmpeg-1.4-py3-none-any.whl
  Using cached llvmlite-0.31.0.tar.gz (110 kB)
  Preparing metadata (setup.py) ... done
  Using cached librosa-0.10.0.post1-py3-none-any.whl (252 kB)
  Using cached librosa-0.10.0-py3-none-any.whl (252 kB)
  Using cached librosa-0.9.2-py3-none-any.whl (214 kB)
  Using cached resampy-0.4.2-py3-none-any.whl (3.1 MB)
  Using cached resampy-0.4.1-py3-none-any.whl (3.1 MB)
  Using cached resampy-0.4.0-py3-none-any.whl (3.1 MB)
  Using cached resampy-0.3.1-py3-none-any.whl (3.1 MB)
  error: subproce

In [7]:
!pip uninstall einops

Found existing installation: einops 0.6.0
Uninstalling einops-0.6.0:
  Would remove:
    /usr/local/lib/python3.9/dist-packages/einops-0.6.0-py3.9.egg
Proceed (Y/n)? y
  Successfully uninstalled einops-0.6.0


In [8]:
!pip install einops

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Using cached einops-0.6.0-py3-none-any.whl (41 kB)


In [13]:
!pip install rotary_embedding_torch

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Using cached rotary_embedding_torch-0.2.1-py3-none-any.whl (4.5 kB)


In [18]:
!pip install unidecode

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Using cached Unidecode-1.3.6-py3-none-any.whl (235 kB)


In [3]:
# Imports used through the rest of the notebook.
import torch
import torchaudio
import torch.nn as nn
import torch.nn.functional as F
import tortoise.api

import IPython

from tortoise.api import TextToSpeech
from tortoise.utils.audio import load_audio, load_voice, load_voices

# This will download all the models used by Tortoise from the HuggingFace hub.
tts = TextToSpeech()

In [9]:
# This is the text that will be spoken.
text = "Joining two modalities results in a surprising increase in generalization! What would happen if we combined them all?"

# Here's something for the poetically inclined.. (set text=)
"""
Then took the other, as just as fair,
And having perhaps the better claim,
Because it was grassy and wanted wear;
Though as for that the passing there
Had worn them really about the same,"""

# Pick a "preset mode" to determine quality. Options: {"ultra_fast", "fast" (default), "standard", "high_quality"}. See docs in api.py
preset = "fast"

In [5]:
# Tortoise will attempt to mimic voices you provide. It comes pre-packaged
# with some voices you might recognize.

# Let's list all the voices available. These are just some random clips I've gathered
# from the internet as well as a few voices from the training dataset.
# Feel free to add your own clips to the voices/ folder.
%ls tortoise/voices

IPython.display.Audio('tortoise/voices/tom/1.wav')

angie/      emma/     lj/      rainbow/       train_daws/     train_kennard/
applejack/  freeman/  mol/     snakes/        train_dotrice/  train_lescault/
custom/     geralt/   myself/  tim_reynolds/  train_dreams/   train_mouse/
daniel/     halle/    pat/     tom/           train_empire/   weaver/
deniro/     jlaw/     pat2/    train_atkins/  train_grace/    william/


In [7]:
# Pick one of the voices from the output above
voice = 'train_dotrice'

# Load it and send it through Tortoise.
voice_samples, conditioning_latents = load_voice(voice)
gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents, 
                          preset=preset)
torchaudio.save('generated.wav', gen.squeeze(0).cpu(), 24000)
IPython.display.Audio('generated.wav')

Generating autoregressive samples..


100%|██████████| 6/6 [00:30<00:00,  5.11s/it]


Computing best candidates using CLVP and CVVP


  0%|          | 0/6 [00:00<?, ?it/s]/usr/local/lib/python3.9/dist-packages/torch/utils/checkpoint.py:31: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn("None of the inputs have requires_grad=True. Gradients will be None")
100%|██████████| 6/6 [00:07<00:00,  1.23s/it]


Transforming autoregressive outputs into audio..


100%|██████████| 80/80 [00:19<00:00,  4.20it/s]


In [ ]:
# Tortoise can also generate speech using a random voice. The voice changes each time you execute this!
# (Note: random voices can be prone to strange utterances)
gen = tts.tts_with_preset(text, voice_samples=None, conditioning_latents=None, preset=preset)
torchaudio.save('generated.wav', gen.squeeze(0).cpu(), 24000)
IPython.display.Audio('generated.wav')

Generating autoregressive samples..


100%|██████████| 6/6 [00:33<00:00,  5.64s/it]


In [ ]:
# Optionally, upload use your own voice by running the next two cells. I recommend
# you upload at least 2 audio clips. They must be a WAV file, 6-10 seconds long.
CUSTOM_VOICE_NAME = "custom"

import os
from google.colab import files

custom_voice_folder = f"tortoise/voices/{CUSTOM_VOICE_NAME}"
os.makedirs(custom_voice_folder)
for i, file_data in enumerate(files.upload().values()):
  with open(os.path.join(custom_voice_folder, f'{i}.wav'), 'wb') as f:
    f.write(file_data)

In [7]:
text="Hello,How are you I am donald trump"

In [10]:
# Generate speech with the custotm voice.(trump voice)
voice_samples, conditioning_latents = load_voice(CUSTOM_VOICE_NAME)
gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents, 
                          preset=preset)
torchaudio.save(f'generated-{CUSTOM_VOICE_NAME}.wav', gen.squeeze(0).cpu(), 24000)
IPython.display.Audio(f'generated-{CUSTOM_VOICE_NAME}.wav')

Generating autoregressive samples..


100%|██████████| 6/6 [00:41<00:00,  6.85s/it]


Computing best candidates using CLVP and CVVP


  0%|          | 0/6 [00:00<?, ?it/s]/usr/local/lib/python3.9/dist-packages/torch/utils/checkpoint.py:31: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn("None of the inputs have requires_grad=True. Gradients will be None")
100%|██████████| 6/6 [00:08<00:00,  1.36s/it]


Transforming autoregressive outputs into audio..


100%|██████████| 80/80 [00:18<00:00,  4.42it/s]


In [ ]:
# You can also combine conditioning voices. Combining voices produces a new voice
# with traits from all the parents.
#
# Lets see what it would sound like if Picard and Kirk had a kid with a penchant for philosophy:
voice_samples, conditioning_latents = load_voices(['pat', 'william'])

gen = tts.tts_with_preset("They used to say that if man was meant to fly, he’d have wings. But he did fly. He discovered he had to.", 
                          voice_samples=voice_samples, conditioning_latents=conditioning_latents, 
                          preset=preset)
torchaudio.save('captain_kirkard.wav', gen.squeeze(0).cpu(), 24000)
IPython.display.Audio('captain_kirkard.wav')

In [ ]:
#for longer sentences break it and feed it to the cloner
#below text is a small story
text="She first got a bowl filled with earth, and planted two seeds. She watered it daily. And I saw the seeds sprouted into lovely green leaves. She displayed them for photosynthesis and the leaves’ greenness deepened. Until she suddenly stopped. And the boisterous greenness of her creature slowly withered away."
import re
sentences = re.split('; |, |\. |\n',text)

In [ ]:
sentences

['She first got a bowl filled with earth',
 'and planted two seeds',
 'She watered it daily',
 'And I saw the seeds sprouted into lovely green leaves',
 'She displayed them for photosynthesis and the leaves’ greenness deepened',
 'Until she suddenly stopped',
 'And the boisterous greenness of her creature slowly withered away.']

In [ ]:
voice_samples, conditioning_latents = load_voice(CUSTOM_VOICE_NAME)
for sent in sentences:
  gen = tts.tts_with_preset(sent, voice_samples=voice_samples, conditioning_latents=conditioning_latents, 
                          preset=preset)
  if sentences.index(sent)==0:
    full_story=gen
  else:
    full_story=torch.cat((full_story,gen),-1)
torchaudio.save(f'generated-{CUSTOM_VOICE_NAME}.wav', full_story.squeeze(0).cpu(), 24000)
IPython.display.Audio(f'generated-{CUSTOM_VOICE_NAME}.wav')

Generating autoregressive samples..


100%|██████████| 6/6 [00:11<00:00,  1.85s/it]


Computing best candidates using CLVP and CVVP


100%|██████████| 6/6 [00:06<00:00,  1.16s/it]


Transforming autoregressive outputs into audio..


...

100%|██████████| 6/6 [00:19<00:00,  3.19s/it]


Computing best candidates using CLVP and CVVP


100%|██████████| 6/6 [00:07<00:00,  1.18s/it]


Transforming autoregressive outputs into audio..


100%|██████████| 80/80 [00:08<00:00,  9.69it/s]


In [ ]:
#Get the input wav file from the user and convert the speech to text and apply it to the cloner
import locale
locale.getpreferredencoding=lambda:"UTF-8"

In [ ]:
!pip3 install SpeechRecognition

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 32.8/32.8 MB 41.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.8/62.8 KB 8.0 MB/s eta 0:00:00
  Attempting uninstall: requests
    Found existing installation: requests 2.25.1
    Uninstalling requests-2.25.1:
      Successfully uninstalled requests-2.25.1


In [ ]:
import speech_recognition as sr

In [ ]:
r=sr.Recognizer()

In [ ]:
with sr.AudioFile("/content/tortoise-tts/trump10.wav") as source:
  audio_data=r.record(source)
  text=r.recognize_google(audio_data)
  print(text)

result2:
{   'alternative': [   {   'confidence': 0.95423949,
                           'transcript': "play I'll sign an executive order "
                                         'that directs the federal government '
                                         'to replace outdated and really '
                                         "outdated it's called"},
                       {   'transcript': 'play outside and executive order '
                                         'that directs the federal government '
                                         'to replace outdated and really '
                                         "outdated it's called"},
                       {   'transcript': "play I'll sign an executive order "
                                         'that directs the federal government '
                                         'to replace outdated and really '
                                         "outdated it's called the"},
                       {   'transcript

In [ ]:
!pip3 install pydub

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
#for larger files
import speech_recognition as sr
from pydub import AudioSegment
from pydub.silence import split_on_silence
import os
r=sr.Recognizer()
sound=AudioSegment.from_wav("/content/Longer voice.wav")
chunks=split_on_silence(sound,min_silence_len=700,silence_thresh=sound.dBFS-14,keep_silence=500) #change the min_silence_len and other parameter according to the audio file
full_text=""
for i,audio_chunk in enumerate(chunks,start=1):
  audio_chunk.export("file: "+str(i),format="wav")
  with sr.AudioFile("file: "+str(i)) as source:
    audio_listened=r.record(source)
    try:
      text=r.recognize_google(audio_listened)
    except sr.UnknownValueError as e:
      print("Error: ",str(e))
    else:
      text=f"{text.capitalize()}."
      print("Chunk: "+str(i),text)
      full_text+=text
      if os.path.exists("file: "+str(i)):
        os.remove("file: "+str(i))
print(full_text)

result2:
{   'alternative': [   {   'confidence': 0.91481024,
                           'transcript': 'she first got a bowl filled with '
                                         'Earth and planted two SE'},
                       {   'transcript': 'she first got a bowl filled with '
                                         'Earth and planted two seed'},
                       {   'transcript': 'she first got a bull filled with '
                                         'Earth and planted two SE'},
                       {   'transcript': 'she first got a bull filled with '
                                         'Earth and planted two seed'},
                       {   'transcript': 'she first got a ball filled with '
                                         'Earth and planted two SE'}],
    'final': True}
Chunk: 1 She first got a bowl filled with earth and planted two se.
result2:
{   'alternative': [   {   'confidence': 0.94866872,
                           'transcript': 'she wan

In [ ]:
full_text

'She first got a bowl filled with earth and planted two se.She wanted a daily and i saw the seeds sprouted into lovely green leaf she displayed them for photosynthesis and the leaves greenness deep.Until she suddenly stop.And the boisterous greenness of a creature slowly with other way.'

### Video Creation

In [ ]:
!pip install yake

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.2/60.2 kB 2.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 62.6 MB/s eta 0:00:00


In [ ]:
!git clone https://gist.github.com/yrevar/942d3a0ac09ec9e5eb3a

Cloning into '942d3a0ac09ec9e5eb3a'...
remote: Enumerating objects: 6, done.
remote: Total 6 (delta 0), reused 0 (delta 0), pack-reused 6
Unpacking objects: 100% (6/6), 13.22 KiB | 6.61 MiB/s, done.


### Removing the stop words and non picturable text

In [ ]:
import nltk
from nltk.corpus import stopwords

text = "Cab has arrived near the bakery"

# Download stopwords if not already downloaded
nltk.download('stopwords')

# Get list of stopwords
stop_words = set(stopwords.words('english'))

# Tokenize text and remove stopwords
words = [word for word in text.split() if word.lower() not in stop_words]

print(words)

['Cab', 'arrived', 'near', 'bakery']


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


In [ ]:
import pandas as pd
df=pd.read_csv("/content/942d3a0ac09ec9e5eb3a/imagenet1000_clsidx_to_labels.txt",sep=":")
df.loc[len(df.index)]=[1000,df.index[1]]
df.columns=["0","text"]
df["text"]=df["text"].apply(lambda x:str(x))
df.drop("0",axis=1,inplace=True)
df["text"]=df["text"].apply(lambda x:x.split(","))
l=list()
for i in df["text"]:
    for j in i:
       if len(j)!=0:
            j=j.replace(" ","")
            l.append(j.replace("'",""))

In [ ]:
for i in range(len(l)):
    l[i]=l[i].lower()

In [ ]:
for i in words:
    if i.lower() in l:
        print(i,"Picturable word")
    else:
        print(i,"Non Picturable word")

Cab Picturable word
arrived Non Picturable word
near Non Picturable word
bakery Picturable word


In [ ]:
os.mkdir("download")
os.mkdir("final")

In [ ]:
import requests
import json
from PIL import Image

import yake

def get_keywords(text=""):
    language = "en"
    max_ngram_size = 2
    deduplication_threshold = 0.9
    numOfKeywords = 20
    custom_kw_extractor = yake.KeywordExtractor(
        lan=language, n=max_ngram_size, dedupLim=deduplication_threshold,
        top=numOfKeywords, features=None)

    keywords = custom_kw_extractor.extract_keywords(text)

    important_keywords = []

    for x in keywords:
        important_keywords.append(x[0])
    
    important_keywords = [word for word in important_keywords if word.lower() not in stop_words]

    return important_keywords


def download_images_from_text(text=""):
    keywords = get_keywords(text)

    print("Keywords: ", keywords)

    i = 1
    for x in keywords:
        response_API = requests.get(
            'https://pixabay.com/api/?key=15716545-91ad30cdd29a591102af58e97&q='
            + x.replace(" ", "+"))

        data = response_API.text
        parse_json = json.loads(data)
        img_url = parse_json['hits'][0]['largeImageURL']
        img = Image.open(requests.get(img_url, stream=True).raw)
        img.save('download/' + str(i) + ".png")
        i += 1

In [ ]:
import cv2
from PIL import Image
import os

img_array = []

final_file_name = "project_1.avi"
path = "download"

height = 480
width = 640


#text = "Software development refers to a set of computer science activities dedicated to the process of creating, designing, deploying and supporting software."

text="She first got a bowl filled with earth, and planted two seeds. She watered it daily."

download_images_from_text(text)

num_of_images = len(os.listdir(path))
print(num_of_images)

for file in os.listdir(path):
    print(file)
    if file.endswith(".png"):
        im = Image.open(os.path.join("download", file))

        imResize = im.resize((width, height), Image.ANTIALIAS)
        imResize.save("final" + file)  # setting quality

image_folder = "final"

images = [os.path.join(image_folder, img) for img in os.listdir(image_folder)
          if img.endswith("png")]

images.sort(key=len)
print(images)


# 1/2 seconds becoz we are separating 2 words from text. so 0.5 img per second
video = cv2.VideoWriter(
    final_file_name, 0, 1/2, (640, 480))

for image in images:
    video.write(cv2.imread(image))

cv2.destroyAllWindows()
video.release()


Keywords:  ['bowl filled', 'earth', 'seeds', 'bowl', 'filled', 'planted', 'daily', 'watered']
15
2.png
15.png
9.png
7.png
11.png
12.png
3.png
13.png
1.png
5.png
10.png
14.png
4.png
6.png
8.png
['final/2.png', 'final/9.png', 'final/7.png', 'final/3.png', 'final/1.png', 'final/5.png', 'final/4.png', 'final/6.png', 'final/8.png', 'final/15.png', 'final/11.png', 'final/12.png', 'final/13.png', 'final/10.png', 'final/14.png']


In [ ]:
vid_capture=cv2.VideoCapture("/content/project_1.avi")

In [ ]:
print("(width,height)",vid_capture.get(3),vid_capture.get(4))

(width,height) 0.0 0.0


In [ ]:
vid_capture.get(5) #fps

0.5

In [ ]:
text="She first got a bowl filled with earth, and planted two seeds. She watered it daily. And I saw the seeds sprouted into lovely green leaves. She displayed them for photosynthesis and the leaves’ greenness deepened. Until she suddenly stopped. And the boisterous greenness of her creature slowly withered away."